In [1]:
import pandas as pd
from data.utils.NCBI.data_loader import NCBIDataLoader
import os
from Bio import Entrez
import urllib
import gzip
import shutil

seems like the current fetcher is not good

... instead of using acession we need to use project ID

from Josefa:
think i found it:
here is a summary for the bioprojectID to ftp path:
https://ftp.ncbi.nlm.nih.gov/genomes/genbank/assembly_summary_genbank.txt

so you'll need the bioproject id (PRJDA40637) and not the accession number (AP011548)

for the example you'll get this ftp path https://ftp.ncbi.nlm.nih.gov/genomes/all/GCA/000/011/045/GCA_000011045.1_ASM1104v1/
and there you can download the gbff file

(https://ftp.ncbi.nlm.nih.gov/genomes/all/GCA/000/011/045/GCA_000011045.1_ASM1104v1/GCA_000011045.1_ASM1104v1_genomic.gbff.gz)

1) download the genbank/assembly_summary_genbank.txt
2) load genome information of HGTREE version 1.0 and add new column to ftp path
3) download all of hgtree and then we good

1.

In [2]:
# get this reference file first
urllib.request.urlretrieve('ftp://ftp.ncbi.nlm.nih.gov/genomes/genbank/assembly_summary_genbank.txt', 'data/HGTREE/version_1/assembly_summary_genbank.txt')

('data/HGTREE/version_1/assembly_summary_genbank.txt',
 <http.client.HTTPMessage at 0x7f82c4962e50>)

In [3]:
urllib.request.urlretrieve('ftp://ftp.ncbi.nlm.nih.gov/genomes/genbank/assembly_summary_genbank_historical.txt', 'data/HGTREE/version_1/assembly_summary_genbank_historical.txt')

('data/HGTREE/version_1/assembly_summary_genbank_historical.txt',
 <http.client.HTTPMessage at 0x7f72bc5ba250>)

2.

In [4]:
assembly_ref = pd.read_csv('data/HGTREE/version_1/assembly_summary_genbank.txt', sep='\t', skiprows=1)

In [5]:
assembly_ref

#assembly_accession  bioproject       biosample         wgs_master   
0           GCA_000001905.1  PRJNA12569    SAMN02953622     AAGU00000000.3  \
1           GCA_000006665.1    PRJNA259    SAMN02604092                 na   
2           GCA_000006765.1    PRJNA331    SAMN02603714                 na   
3           GCA_000006865.1     PRJNA72    SAMN02603339                 na   
4           GCA_000006965.1     PRJNA19    SAMEA3283068                 na   
...                     ...         ...             ...                ...   
1860018     GCA_958328925.1  PRJEB64161  SAMEA114026231  CATUFM000000000.1   
1860019     GCA_958327055.1  PRJEB64161  SAMEA114026232  CATTYJ000000000.1   
1860020     GCA_958328845.1  PRJEB64161  SAMEA114026236  CATUFE000000000.1   
1860021     GCA_958325635.1  PRJEB64161  SAMEA114026239  CATTSV000000000.1   
1860022     GCA_958324945.1  PRJEB64161  SAMEA114026248  CATTQB000000000.1   

               refseq_category   taxid  species_taxid   
0        representative genome    9785           9785  \
1                           na  155864            562   
2             reference genome  208964            287   
3                           na  272623           1358   
4                           na  266834            382   
...                        ...     ...            ...   
1860018                     na     562            562   
1860019                     na     562            562   
1860020                     na     562            562   
1860021                     na     562            562   
1860022                     na     562            562   

                                   organism_name infraspecific_name   
0                             Loxodonta africana                 na  \
1           Escherichia coli O157:H7 str. EDL933      strain=EDL933   
2                    Pseudomonas aeruginosa PAO1        strain=PAO1   
3        Lactococcus lactis subsp. lactis Il1403      strain=IL1403   
4                    Sinorhizobium meliloti 1021        strain=1021   
...                                          ...                ...   
1860018                         Escherichia coli                 na   
1860019                         Escherichia coli                 na   
1860020                         Escherichia coli                 na   
1860021                         Escherichia coli                 na   
1860022                         Escherichia coli                 na   

                 isolate  ... replicon_count scaffold_count contig_count   
0             ISIS603380  ...              1           2352        95866  \
1                     na  ...              2              2            2   
2                     na  ...              1              1            1   
3                     na  ...              1              1            1   
4                     na  ...              3              3            3   
...                  ...  ...            ...            ...          ...   
1860018  SAP2596_300bp_1  ...              0            181          181   
1860019  SAP2597_300bp_1  ...              0            252          252   
1860020  SAP2603_300bp_1  ...              0            158          158   
1860021  SAP2236_300bp_1  ...              0            130          130   
1860022  SAP2307_300bp_1  ...              0            152          152   

              annotation_provider   
0                              na  \
1                 Univ. Wisconsin   
2        PathoGenesis Corporation   
3                            INRA   
4                          MELILO   
...                           ...   
1860018                        na   
1860019                        na   
1860020                        na   
1860021                        na   
1860022                        na   

                                          annotation_name annotation_date   
0                                                      na              na  \
1                 Ann

In [6]:
assembly_ref_old = pd.read_csv('data/HGTREE/version_1/assembly_summary_genbank_historical.txt', sep='\t', skiprows=1)

In [7]:
assembly_ref_old

#assembly_accession   bioproject     biosample         wgs_master   
0         GCA_000001405.1   PRJNA31257            na                 na  \
1         GCA_000003205.1   PRJNA12555  SAMN02898106     AAFC00000000.3   
2         GCA_000003525.1   PRJNA29171  SAMN02953741     ACBT00000000.1   
3         GCA_000249215.1   PRJNA50919  SAMN00116898     AIFC00000000.1   
4         GCA_000011965.1     PRJNA281  SAMN02604003                 na   
...                   ...          ...           ...                ...   
55086     GCA_031059035.1  PRJNA242847  SAMN37214848  ABLXOH000000000.1   
55087     GCA_031242935.1           na            na                 na   
55088     GCA_031313955.1           na            na                 na   
55089     GCA_031322045.1           na            na                 na   
55090     GCA_903970745.1   PRJEB35957  SAMEA6435259  CAJCJS000000000.1   

      refseq_category    taxid  species_taxid   
0                  na     9606           9606  \
1                  na     9913           9913   
2                  na   559297           5039   
3                  na   868141            562   
4                  na   246200          89184   
...               ...      ...            ...   
55086              na      595          28901   
55087              na  2812862        2812862   
55088              na  2936916        2936916   
55089              na  3017776        3017776   
55090              na  2103321        2103321   

                                           organism_name   infraspecific_name   
0                                           Homo sapiens                   na  \
1                                             Bos taurus       breed=Hereford   
2                          Blastomyces dermatitidis ER-3          strain=ER-3   
3                                 Escherichia coli DEC2D         strain=DEC2D   
4                                Ruegeria pomeroyi DSS-3         strain=DSS-3   
...                                                  ...                  ...   
55086  Salmonella enterica subsp. enterica serovar In...  strain=FSIS22314091   
55087                     Clostridium phage HZhang-2021a                   na   
55088                      Chryseobacterium phage MA9V-1                   na   
55089                           Salmonella phage LPSent1                   na   
55090                      Orchesella sp. BIOUG14422-C09                   na   

      isolate  ... replicon_count scaffold_count contig_count   
0          na  ...             24            249        27054  \
1          na  ...             30          14188       131430   
2          na  ...              1             27          593   
3          na  ...              0             45           45   
4          na  ...              2              2            2   
...       ...  ...            ...            ...          ...   
55086      na  ...              0            143          143   
55087      na  ...              1              1            1   
55088      na  ...              1              1            1   
55089      na  ...              1              1            1   
55090      na  ...              7          42596        42596   

                                     annotation_provider   
0                                                     na  \
1                                                     na   
2                                                     na   
3                                                     na   
4                                                     na   
...                                                  ...   
55086                                               NCBI   
55087  Jiangsu Academy of Agricultural Sciences, Inst...   
55088  The Faculty of Life Science and Technology, Ku...   
55089                                                 na   
55090                                                 na   

                                         

In [20]:
# get this reference file first
urllib.request.urlretrieve('ftp://ftp.ncbi.nlm.nih.gov/genomes/refseq/bacteria/assembly_summary.txt', 'data/HGTREE/version_1/assembly_summary.txt')

('data/HGTREE/version_1/assembly_summary.txt',
 <http.client.HTTPMessage at 0x7f62b58a8310>)

In [21]:
assembly_sum = pd.read_csv('data/HGTREE/version_1/assembly_summary.txt', sep='\t', skiprows=1)

In [22]:
assembly_sum

#assembly_accession   bioproject       biosample         wgs_master   
0          GCF_900128725.1  PRJNA224116    SAMEA4556317                 na  \
1          GCF_948107705.1  PRJNA224116  SAMEA112293847  CANUFE000000000.1   
2          GCF_008244535.1  PRJNA224116    SAMN12634886     VTFL00000000.1   
3          GCF_026418735.1  PRJNA224116    SAMN30305022  JAOAAT000000000.1   
4          GCF_003854875.1  PRJNA224116    SAMN10058823                 na   
...                    ...          ...             ...                ...   
313352     GCF_031195445.1  PRJNA224116    SAMN37171699                 na   
313353     GCF_031157525.1  PRJNA224116    SAMN35527782  JAVIXR000000000.1   
313354     GCF_031199965.1  PRJNA224116    SAMN37187764                 na   
313355     GCF_031326225.1  PRJNA224116    SAMN37256830                 na   
313356     GCF_031326205.1  PRJNA224116    SAMN37256843                 na   

       refseq_category    taxid  species_taxid                 organism_name   
0                   na        9              9           Buchnera aphidicola  \
1                   na        9              9           Buchnera aphidicola   
2                   na       14             14     Dictyoglomus thermophilum   
3                   na       14             14     Dictyoglomus thermophilum   
4                   na       17             17  Methylophilus methylotrophus   
...                ...      ...            ...                           ...   
313352              na  3072793        3072793       Acuticoccus sp. MNP-M23   
313353              na  3072994        3072994       Marinobacter sp. F26243   
313354              na  3073092        3073092        Paenibacillus sp. D2_2   
313355              na  3073561        3073561    Undibacterium sp. 20NA77.5   
313356              na  3073563        3073563   Flavobacterium sp. 20NA77.7   

         infraspecific_name       isolate  ... replicon_count scaffold_count   
0       strain=BCifornacula          2912  ...              3              3  \
1                        na  Mw16_67_buch  ...              0              4   
2           strain=PYS_80_B            na  ...              0             23   
3                        na        SKW156  ...              0             16   
4                strain=D22            na  ...              1              1   
...                     ...           ...  ...            ...            ...   
313352       strain=MNP-M23            na  ...              7              7   
313353        strain=F26243            na  ...              0             41   
313354          strain=D2_2            na  ...              1              1   
313355      strain=20NA77.5            na  ...              1              1   
313356      strain=20NA77.7            na  ...              1              1   

       contig_count                                annotation_provider   
0                 3                                        NCBI RefSeq  \
1                 4                                        NCBI RefSeq   
2                23                                        NCBI RefSeq   
3                16                                        NCBI RefSeq   
4                 1                                        NCBI RefSeq   
...             ...                                                ...   
313352            7                                        NCBI RefSeq   
313353           41                                        NCBI RefSeq   
313354            1                                        NCBI RefSeq   
313355            1  Korea Research Institute of Bioscience and Bio...   
313356            1                                        NCBI RefSeq   

                                          annotation_name annotation_date   
0       NCBI Prokaryotic Genome Annotation Pipeline (P...        04/26/23  \
1       NCBI Prokaryotic Genome Annotation Pipeline (P...        06/04/23   
2       NCBI Prokaryotic Gen

In [9]:
hgtree_genomes = pd.read_csv('data/HGTREE/version_1/Genome_Information_20150618.txt', sep='\t')

In [10]:
hgtree_genomes

ID                          Genome name   
0     MBS0            Marinobacter sp. BSs20148  \
1     Nsa0  Nitratifractor salsuginis DSM 16511   
2     Vvu2              Vibrio vulnificus CMCP6   
3     Vvu1           Vibrio vulnificus MO6-24/O   
4     Vvu0              Vibrio vulnificus YJ016   
...    ...                                  ...   
2467  Hau0    Herpetosiphon aurantiacus DSM 785   
2468  Mph0       Microlunatus phosphovorus NM-1   
2469  Ani0     Arcobacter nitrofigilis DSM 7299   
2470  Hci0    Helicobacter cinaedi ATCC BAA-847   
2471  Hci1         Helicobacter cinaedi PAGU611   

                                               Taxonomy  Genome size(Mb)   
0     Bacteria; Proteobacteria; Gammaproteobacteria;...             4.06  \
1     Bacteria; Proteobacteria; Epsilonproteobacteri...             2.10   
2     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.13   
3     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.01   
4     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.26   
...                                                 ...              ...   
2467  Bacteria; Chloroflexi; Chloroflexia; Herpetosi...             6.79   
2468  Bacteria; Actinobacteria; Actinobacteridae; Ac...             5.68   
2469  Bacteria; Proteobacteria; Epsilonproteobacteri...             3.19   
2470  Bacteria; Proteobacteria; Epsilonproteobacteri...             2.24   
2471  Bacteria; Proteobacteria; Epsilonproteobacteri...             2.10   

      GC(%) GenBank accession number   BioProject  
0     54.10                 CP003735  PRJNA171995  
1     53.90                 CP002452   PRJNA62183  
2     46.72        AE016795,AE016796   PRJNA62909  
3     46.95        CP002469,CP002470   PRJNA62243  
4     46.67        BA000037,BA000038   PRJNA58007  
...     ...                      ...          ...  
2467  50.89                 CP000875   PRJNA58599  
2468  67.30                 AP012204   PRJNA68055  
2469  28.40                 CP001999   PRJNA49001  
2470  38.30                 AP012492  PRJNA193765  
2471  38.52                 AP012344  PRJDA162219  

[2472 rows x 7 columns]

Unfortunately some bioproject is gone ... need to check how many are gone

In [11]:
ftp_path = []
for bioproj in hgtree_genomes['BioProject']:
    ftp_path.append(assembly_ref[assembly_ref['bioproject']==bioproj]['ftp_path'])

In [17]:
link = assembly_ref[assembly_ref['bioproject']=='PRJDA40637']['ftp_path']
link

1180    https://ftp.ncbi.nlm.nih.gov/genomes/all/GCA/0...
Name: ftp_path, dtype: object

In [14]:
assembly_ref_old[assembly_ref_old['bioproject']=='PRJNA171995']['ftp_path']

Series([], Name: ftp_path, dtype: object)

In [23]:
assembly_sum[assembly_sum['bioproject']=='PRJNA171995']['ftp_path']

Series([], Name: ftp_path, dtype: object)

In [19]:
hgtree_genomes[hgtree_genomes['BioProject'] == 'PRJNA171995']

ID                Genome name   
0  MBS0  Marinobacter sp. BSs20148  \

                                            Taxonomy  Genome size(Mb)  GC(%)   
0  Bacteria; Proteobacteria; Gammaproteobacteria;...             4.06   54.1  \

  GenBank accession number   BioProject  
0                 CP003735  PRJNA171995

In [95]:
print(len(ftp_path))
print(len(hgtree_genomes['BioProject']))

2472
2472


In [106]:
hgtree_genomes['ftp_path'] = ftp_path

In [107]:
hgtree_genomes

ID                          Genome name   
0     MBS0            Marinobacter sp. BSs20148  \
1     Nsa0  Nitratifractor salsuginis DSM 16511   
2     Vvu2              Vibrio vulnificus CMCP6   
3     Vvu1           Vibrio vulnificus MO6-24/O   
4     Vvu0              Vibrio vulnificus YJ016   
...    ...                                  ...   
2467  Hau0    Herpetosiphon aurantiacus DSM 785   
2468  Mph0       Microlunatus phosphovorus NM-1   
2469  Ani0     Arcobacter nitrofigilis DSM 7299   
2470  Hci0    Helicobacter cinaedi ATCC BAA-847   
2471  Hci1         Helicobacter cinaedi PAGU611   

                                               Taxonomy  Genome size(Mb)   
0     Bacteria; Proteobacteria; Gammaproteobacteria;...             4.06  \
1     Bacteria; Proteobacteria; Epsilonproteobacteri...             2.10   
2     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.13   
3     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.01   
4     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.26   
...                                                 ...              ...   
2467  Bacteria; Chloroflexi; Chloroflexia; Herpetosi...             6.79   
2468  Bacteria; Actinobacteria; Actinobacteridae; Ac...             5.68   
2469  Bacteria; Proteobacteria; Epsilonproteobacteri...             3.19   
2470  Bacteria; Proteobacteria; Epsilonproteobacteri...             2.24   
2471  Bacteria; Proteobacteria; Epsilonproteobacteri...             2.10   

      GC(%) GenBank accession number   BioProject   
0     54.10                 CP003735  PRJNA171995  \
1     53.90                 CP002452   PRJNA62183   
2     46.72        AE016795,AE016796   PRJNA62909   
3     46.95        CP002469,CP002470   PRJNA62243   
4     46.67        BA000037,BA000038   PRJNA58007   
...     ...                      ...          ...   
2467  50.89                 CP000875   PRJNA58599   
2468  67.30                 AP012204   PRJNA68055   
2469  28.40                 CP001999   PRJNA49001   
2470  38.30                 AP012492  PRJNA193765   
2471  38.52                 AP012344  PRJDA162219   

                                       ftp_path  
0     Series([], Name: ftp_path, dtype: object)  
1     Series([], Name: ftp_path, dtype: object)  
2     Series([], Name: ftp_path, dtype: object)  
3     Series([], Name: ftp_path, dtype: object)  
4     Series([], Name: ftp_path, dtype: object)  
...                                         ...  
2467  Series([], Name: ftp_path, dtype: object)  
2468  Series([], Name: ftp_path, dtype: object)  
2469  Series([], Name: ftp_path, dtype: object)  
2470  Series([], Name: ftp_path, dtype: object)  
2471  Series([], Name: ftp_path, dtype: object)  

[2472 rows x 8 columns]

In [22]:
MBS0 = NCBIDataLoader('CP003735')

found 1 ids
ftp://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/000/283/275/GCF_000283275.1_ASM28327v1/GCF_000283275.1_ASM28327v1_cds_from_genomic.fna.gz


In [25]:
LrH4 = NCBIDataLoader('AP011548')

found 1 ids
ftp://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/000/011/045/GCF_000011045.1_ASM1104v1/GCF_000011045.1_ASM1104v1_cds_from_genomic.fna.gz


In [18]:
Vvu1_1 = NCBIDataLoader('CP002469')
Vvu1_2 = NCBIDataLoader('CP002470')

found 1 ids
ftp://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/000/186/585/GCF_000186585.1_ASM18658v1/GCF_000186585.1_ASM18658v1_cds_from_genomic.fna.gz
found 1 ids
ftp://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/000/186/585/GCF_000186585.1_ASM18658v1/GCF_000186585.1_ASM18658v1_cds_from_genomic.fna.gz


In [16]:
test_text

ID                          Genome name   
0     MBS0            Marinobacter sp. BSs20148  \
1     Nsa0  Nitratifractor salsuginis DSM 16511   
2     Vvu2              Vibrio vulnificus CMCP6   
3     Vvu1           Vibrio vulnificus MO6-24/O   
4     Vvu0              Vibrio vulnificus YJ016   
...    ...                                  ...   
2467  Hau0    Herpetosiphon aurantiacus DSM 785   
2468  Mph0       Microlunatus phosphovorus NM-1   
2469  Ani0     Arcobacter nitrofigilis DSM 7299   
2470  Hci0    Helicobacter cinaedi ATCC BAA-847   
2471  Hci1         Helicobacter cinaedi PAGU611   

                                               Taxonomy  Genome size(Mb)   
0     Bacteria; Proteobacteria; Gammaproteobacteria;...             4.06  \
1     Bacteria; Proteobacteria; Epsilonproteobacteri...             2.10   
2     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.13   
3     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.01   
4     Bacteria; Proteobacteria; Gammaproteobacteria;...             5.26   
...                                                 ...              ...   
2467  Bacteria; Chloroflexi; Chloroflexia; Herpetosi...             6.79   
2468  Bacteria; Actinobacteria; Actinobacteridae; Ac...             5.68   
2469  Bacteria; Proteobacteria; Epsilonproteobacteri...             3.19   
2470  Bacteria; Proteobacteria; Epsilonproteobacteri...             2.24   
2471  Bacteria; Proteobacteria; Epsilonproteobacteri...             2.10   

      GC(%) GenBank accession number   BioProject  
0     54.10                 CP003735  PRJNA171995  
1     53.90                 CP002452   PRJNA62183  
2     46.72        AE016795,AE016796   PRJNA62909  
3     46.95        CP002469,CP002470   PRJNA62243  
4     46.67        BA000037,BA000038   PRJNA58007  
...     ...                      ...          ...  
2467  50.89                 CP000875   PRJNA58599  
2468  67.30                 AP012204   PRJNA68055  
2469  28.40                 CP001999   PRJNA49001  
2470  38.30                 AP012492  PRJNA193765  
2471  38.52                 AP012344  PRJDA162219  

[2472 rows x 7 columns]

In [2]:
test = pd.read_excel('data/HGTREE/version_1/Dataset S1.xlsx')

In [27]:
test

Gene set ID                                        Protein IDs   
0       Gene_ID_91069  ACT73777;CCG33250;AHA67163;ADM40533;ACI07695;A...  \
1      Gene_ID_139572  ABQ39645;ABG65173;ADU42495;CAL74406;ADZ68757;A...   
2      Gene_ID_149322  AEH87228;AFO89768;ACI52537;ABE64668;AHD02161;A...   
3      Gene_ID_136070  ABM42395;ACK53754;ABE31734;CCH12119;ABX36784;C...   
4       Gene_ID_39191  ADO11396;CAD83531;ADT77374;ACT41261;CAX57476;A...   
...               ...                                                ...   
69360  Gene_ID_125500  AGS04095;CCP47798;CAH63662;AEG86243;AGE74794;A...   
69361   Gene_ID_69599  AGR62980;AGV57273;BAM98444;AFI06446;AFV97007;A...   
69362   Gene_ID_57373  AGS01115;CCE13409;AGT70710;AFS24625;ACZ33279;A...   
69363   Gene_ID_18249  BAI54015;CBG23601;AHB43288;AEG35312;AGK67905;A...   
69364   Gene_ID_16865  CAR16520;BAI53819;AER82997;ACB01471;CAD05045;A...   

              PFAM IDs                                  PFAM Descriptions   
0              PF01165                              Ribosomal protein S21  \
1      PF00589;PF13356  Phage integrase family;Domain of unknown funct...   
2      PF02371;PF01548   Transposase IS116/IS110/IS902 family;Transposase   
3                  NaN                                                NaN   
4              PF00137                             ATP synthase subunit C   
...                ...                                                ...   
69360          PF01235                    Sodium:alanine symporter family   
69361          PF06429  Flagellar basal body rod FlgEFG protein C-term...   
69362          PF00676                         Dehydrogenase E1 component   
69363          PF00860                                    Permease family   
69364  PF12833;PF12852                      Helix-turn-helix domain;Cupin   

                  GO ID (BP)                         GO Description (BP)   
0                 GO:0006412                                 translation  \
1      GO:0006310;GO:0015074           DNA recombination;DNA integration   
2                 GO:0006313                 transposition, DNA-mediated   
3                        NaN                                         NaN   
4                 GO:0015991     ATP hydrolysis coupled proton transport   
...                      ...                                         ...   
69360  GO:0032328;GO:0006814      alanine transport;sodium ion transport   
69361                    NaN                                         NaN   
69362             GO:0008152                           metabolic process   
69363  GO:0006810;GO:0055085           transport;transmembrane transport   
69364             GO:0006355  regulation of transcription, DNA-dependent   

       GO ID (CC)                                GO Description (CC)   
0      GO:0005840                                           ribosome  \
1             NaN                                                NaN   
2             NaN                                                NaN   
3             NaN                                                NaN   
4      GO:0033177  proton-transporting two-sector ATPase complex,...   
...           ...                                                ...   
69360  GO:0016020                                           membrane   
69361         NaN                                                NaN   
69362         NaN                                                NaN   
69363  GO:0016020                                           membrane   
69364         NaN                                                NaN   

                  GO ID (MF)   
0                 GO:0003735  \
1                 GO:0003677   
2      GO:0004803;GO:0003677   
3                        NaN   
4                 GO:0015078   
...                      ...   
69360             GO:0015655   
69361                    NaN   
69362             GO:0016624   
69363             GO:0005215   
69364  GO:0003700;GO:0043565   

         

In [19]:
list_of_hgts = test['Protein IDs'][0].split(';')

In [26]:
LrH4.genes

{'LRHM_RS00005': {'gene': 'dnaA',
  'protein': 'chromosomal replication initiator protein DnaA',
  'location': '1..1350',
  'g_count': 297,
  'a_count': 414,
  'c_count': 321,
  't_count': 318,
  'GC1': 55.77777777777778,
  'SD1': 0.26440071927858055,
  'GC2': 31.77777777777778,
  'SD2': -1.3056645378233978,
  'GC3': 49.77777777777778,
  'SD3': 0.2762956083476491,
  'GCT': 45.77777777777778,
  'SDT': -0.3037833445319484,
  'rel_freq': {'G': 0.22,
   'A': 0.30666666666666664,
   'C': 0.23777777777777778,
   'T': 0.23555555555555555},
  '12_symbols': {'A': [0.30666666666666664,
    0.3888888888888889,
    0.22444444444444445],
   'T': [0.13555555555555557, 0.29333333333333333, 0.2777777777777778],
   'G': [0.3377777777777778, 0.10666666666666667, 0.21555555555555556],
   'C': [0.22, 0.2111111111111111, 0.2822222222222222]},
  '48_symbols': {'AA': [0.13111111111111112,
    0.14222222222222222,
    0.07126948775055679],
   'AG': [0.017777777777777778, 0.06666666666666667, 0.080178173719376

In [20]:
if '' in list_of_hgts:
    print(yes)

['ACT73777',
 'CCG33250',
 'AHA67163',
 'ADM40533',
 'ACI07695',
 'AER86047',
 'AEG95669',
 'CAO95463',
 'AGJ89067',
 'AGU65987',
 'AAZ89784',
 'ADT76700',
 'ACH75335',
 'AAV78912',
 'ADF63926',
 'CAR00027',
 'CAQ90499',
 'ABG71138',
 'ACA76310',
 'ACY90289',
 'CBY25674',
 'BAO00272',
 'AEJ99970',
 'AGG32337',
 'BAE77116',
 'AEF47500',
 'AGE84966',
 'BAK12713',
 'ADZ43873',
 'ACB16099',
 'BAI32463',
 'AGH72577',
 'AFG41992',
 'ACT27745',
 'AEZ46941',
 'ADN47947',
 'AEN66455',
 'CDG09258',
 'ABS48627',
 'AEQ14316',
 'AEZ42173',
 'ACY83303',
 'ACT11605',
 'BAH65245',
 'AGS31310',
 'ABV07476',
 'BAN98221',
 'AGQ78744',
 'AGX39491',
 'ADW00368',
 'BAB37371',
 'CAR44682',
 'AGF83779',
 'CAX54179',
 'CAL19322',
 'AGC88544',
 'AEG30159',
 'AFP85027',
 'CBA19367',
 'AFP85673',
 'CBJ47677',
 'ADO46973',
 'AFS88119',
 'AEW44719',
 'ACR61794',
 'AEL71050',
 'ACX38322',
 'ADX19000',
 'CCW75905',
 'BAI56449',
 'BAI37668',
 'AFR01978',
 'ACN47370',
 'AFS72654',
 'AAS63139',
 'AGQ66606',
 'ACF90190',

# TEST

('data/NCBI/sequence_files/assembly_summary_genbank.txt',
 <http.client.HTTPMessage at 0x7f1a702f14d0>)

In [87]:
assembly_ref[assembly_ref['bioproject']=='PRJDA40637']['ftp_path']

850    https://ftp.ncbi.nlm.nih.gov/genomes/all/GCA/0...
Name: ftp_path, dtype: object

In [47]:
SEQUENCES_FOLDER = 'data/NCBI/sequence_files'

In [71]:
def get_assembly_summary_2(id):
        """Get esummary for an entrez id"""
        esummary_handle = Entrez.esummary(db="assembly", id=id, report="full")
        esummary_record = Entrez.read(esummary_handle)
        return esummary_record

In [86]:
handle = Entrez.esearch(db="assembly", term='GCA_000011045.1', retmax='200')
record = Entrez.read(handle)
ids = record['IdList']
print (f'found {len(ids)} ids')
for id in ids:
    summary = get_assembly_summary_2(id)
    url = summary['DocumentSummarySet']['DocumentSummary'][0]['FtpPath_RefSeq']
    if url == '':
        continue
    print(url)
        

found 1 ids
ftp://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/000/011/045/GCF_000011045.1_ASM1104v1


In [75]:
print(len(summary))

1


In [48]:
def get_assembly_summary(id):
        """Get esummary for an entrez id"""
        esummary_handle = Entrez.esummary(db="assembly", id=id, report="full")
        esummary_record = Entrez.read(esummary_handle)
        return esummary_record

In [54]:
def download_genome( name, file_type):
        #def get_assemblies(term, download=True, path='sequence_files'):
        """Download genbank assemblies for a given search term.
        https://dmnfarrell.github.io/bioinformatics/assemblies-genbank-python
        Args:
            term: search term, usually organism name
            download: whether to download the results
            path: folder to save to
        """

        #provide your own mail here
        Entrez.email = "adjie.salman@stud.uni-due.de"
        Entrez.api_key = "726c2709d1827c981a38403d4a7d99e5cf08"
        handle = Entrez.esearch(db="assembly", term=name, retmax='200')
        record = Entrez.read(handle)
        ids = record['IdList']
        print (f'found {len(ids)} ids')
        links = []
        for id in ids:
            #get summary
            summary = get_assembly_summary(id)
            #get ftp link
            url = summary['DocumentSummarySet']['DocumentSummary'][0]['FtpPath_RefSeq']
            if url == '':
                continue
            label = os.path.basename(url)
            #get the fasta link - change this to get other formats
            if file_type == 'fna':
                link = os.path.join(url,label+'_cds_from_genomic.fna.gz')
                print (link)
                links.append(link)
                if not os.path.isfile(SEQUENCES_FOLDER+f'/{name}.fna'):
                    #download link
                    urllib.request.urlretrieve(link, SEQUENCES_FOLDER+f'/{name}.fna.gz')
                    with gzip.open(SEQUENCES_FOLDER+f'/{name}.fna.gz', 'rb') as f_in:
                        with open(SEQUENCES_FOLDER+f'/{name}.fna', 'wb') as f_out:
                            shutil.copyfileobj(f_in, f_out)
                    os.remove(SEQUENCES_FOLDER+f'/{name}.fna.gz')
            elif file_type == 'gbff':
                link = os.path.join(url,label+'_genomic.gbff.gz')
                print (link)
                links.append(link)
                if not os.path.isfile(SEQUENCES_FOLDER+f'/{name}.gbff'):
                    #download link
                    urllib.request.urlretrieve(link, SEQUENCES_FOLDER+f'/{name}.gbff.gz')
                    with gzip.open(SEQUENCES_FOLDER+f'/{name}.gbff.gz', 'rb') as f_in:
                        with open(SEQUENCES_FOLDER+f'/{name}.gbff', 'wb') as f_out:
                            shutil.copyfileobj(f_in, f_out)
                    os.remove(SEQUENCES_FOLDER+f'/{name}.gbff.gz')
            elif file_type =='gpff':
                link = os.path.join(url,label+'_protein.gpff.gz')
                print (link)
                links.append(link)
                if not os.path.isfile(SEQUENCES_FOLDER+f'/{name}.gpff'):
                    #download link
                    urllib.request.urlretrieve(link, SEQUENCES_FOLDER+f'/{name}.gpff.gz')
                    with gzip.open(SEQUENCES_FOLDER+f'/{name}.gpff.gz', 'rb') as f_in:
                        with open(SEQUENCES_FOLDER+f'/{name}.gpff', 'wb') as f_out:
                            shutil.copyfileobj(f_in, f_out)
                    os.remove(SEQUENCES_FOLDER+f'/{name}.gpff.gz')
            elif file_type =='gff':
                link = os.path.join(url,label+'_genomic.gff.gz')
                print (link)
                links.append(link)
                if not os.path.isfile(SEQUENCES_FOLDER+f'/{name}.gff'):
                    #download link
                    urllib.request.urlretrieve(link, SEQUENCES_FOLDER+f'/{name}.gff.gz')
                    with gzip.open(SEQUENCES_FOLDER+f'/{name}.gff.gz', 'rb') as f_in:
                        with open(SEQUENCES_FOLDER+f'/{name}.gff', 'wb') as f_out:
                            shutil.copyfileobj(f_in, f_out)
                    os.remove(SEQUENCES_FOLDER+f'/{name}.gff.gz')

In [85]:
test_dl = download_genome('GCA_000011045.1', 'gbff')

found 1 ids
ftp://ftp.ncbi.nlm.nih.gov/genomes/all/GCF/000/011/045/GCF_000011045.1_ASM1104v1/GCF_000011045.1_ASM1104v1_genomic.gbff.gz
